This notebook is an analysis of frame times received by the Pi. The trial is started and stopped and frames are generated with a Teensy running code in ~/pie/platformio/simScope. Frames are genrated at a 30 ms interval.

Bottom line is that Python time is not accurate. Python time is required to log incoming frame times when using the Raspberry GPIO package.

To acheive better, sub-millisecond, accuracy, the pigpio package must be used. The PiE server will use pigpio if its daemon (pigpiod) is running and will fallback to GPIO if it is not.

### Raspberry GPIO Package

https://sourceforge.net/p/raspberry-gpio-python/wiki/Home/

### Pigpio (see install instructions and how to run pigpiod)

http://abyz.me.uk/rpi/pigpio/

### Important

Missed GPIO frames occur when the Pi is busy doing somehting else. During recording, limit your interaction with the Pi and in particular the web interface to the PiE server.


## Load trial file from PiE server

In [2]:
import os
import pandas as pd
import numpy as np

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.plotly as py
import plotly.graph_objs as go

init_notebook_mode(connected=True)

import urllib2 # python 2
from StringIO import StringIO # python 2

# Read the trial file from a url on the local PiE server
"""
url = 'http://192.168.1.15:5010/videolist/home/pi/video/20180805/20180805_190456_t1.txt'
response = urllib2.urlopen(url).read()
html = StringIO(response)
"""

# Read the trial file from a local server mount.
# This assumes the Pi is running a file server (afp or smb)
html = '/Volumes/pi15/video/20180902/20180902_185920_t3.txt'
df = pd.read_csv(html, header=1)

frame_df = df.loc[df['event'].isin(['frame'])]

frame_df = df[ df['event'].isin(['frame']) ]
#frame_df = frame_df[ frame_df['lastFrameInterval'] != '0']

print 'Number of frames generated by Teensy running (30 seconds) simScope = 998'
print 'Number of frames generated by Teensy running (60 seconds) simScope = 1998'
print 'Number of frames generated by Teensy running (300 seconds) simScope = 9992'
print 'Number of frames PiE server running on Raspberry detected = ', frame_df.shape[0]

frame_df[0:9]


Number of frames generated by Teensy running (30 seconds) simScope = 998
Number of frames generated by Teensy running (60 seconds) simScope = 1998
Number of frames generated by Teensy running (300 seconds) simScope = 9992
Number of frames PiE server running on Raspberry detected =  9992


date      time  linuxSeconds  secondsSinceStart  event value      str  \
4   20180902  18:59:20  1.535929e+09           0.157021  frame     1  4497581   
5   20180902  18:59:20  1.535929e+09           0.186879  frame     2  4530898   
6   20180902  18:59:20  1.535929e+09           0.217552  frame     3  4564213   
7   20180902  18:59:20  1.535929e+09           0.247236  frame     4  4597529   
8   20180902  18:59:20  1.535929e+09           0.276841  frame     5  4630845   
9   20180902  18:59:20  1.535929e+09           0.307609  frame     6  4664159   
10  20180902  18:59:20  1.535929e+09           0.337181  frame     7  4697475   
11  20180902  18:59:20  1.535929e+09           0.367439  frame     8  4730790   
12  20180902  18:59:20  1.535929e+09           0.397000  frame     9  4730790   

           tick  
4   3355260.294  
5   3355290.295  
6   3355320.295  
7     3355350.3  
8     3355380.3  
9   3355410.305  
10  3355440.305  
11   3355470.31  
12   3355500.31

## Plot the frame time versus frame number.

Looks pretty good, right?

In [11]:
timeData = {
        'x': frame_df.value, 
        'y': frame_df.secondsSinceStart, 
        'text': '', 
        'mode': 'markers', 
        'name': ''
    }

fig = {
    'data': [timeData],
    'layout': {
        'xaxis': {'title': 'Frame Number'},
        'yaxis': {'title': "Seconds Since Start (sec)"}
    }
}

iplot(fig, filename='pandas/multiple-scatter0')

## Plot the inter-frame-interval

Frame arrival times and in turn frame intervals are sub millisecond accurate using the pigpio package (and its daemon pigpiod). Timing is not accurate when using the GPIO and standard time packages.

In [16]:
# gpio and standard python time
frameInterval_time = np.diff( frame_df['secondsSinceStart'].astype(float).values )
# pigpio
frameInterval_pigpio = np.diff( frame_df['tick'].astype(float).values ) / 1000

pigpioData = {
        'x': frame_df.value, 
        'y': frameInterval_pigpio, 
        'text': '', 
        'mode': 'markers', 
        'name': 'pigpio tick'
    }

timeData = {
        'x': frame_df.value, 
        'y': frameInterval_time, 
        'text': '', 
        'mode': 'markers', 
        'name': 'python time'
    }

fig = {
    'data': [timeData, pigpioData],
    'layout': {
        'xaxis': {'title': 'Frame Number'},
        'yaxis': {'title': "Inter-Frame-Interval (seconds)"}
    }
}

iplot(fig, filename='pandas/multiple-scatter1')

## Plot a histogram of frame intervals

Pigpio is more accurate than GPIO and standard time.

Note, for larger datasets (5 minutes of recording 30 fps) this plot is not displaying?

In [18]:
timeHist = go.Histogram(x=frameInterval_time, name = "python time")
pigpioHist = go.Histogram(x=frameInterval_pigpio, name = "pigpio tick")

fig = {
    'data': [timeHist, pigpioHist],
    'layout': {
        'xaxis': {'title': 'Inter-Frame-Interval (seconds)'},
        'yaxis': {'title': "Count", 'type': "log"}
    }
}

iplot(fig, filename='pandas/multiple-scatter2')

## Shot plot of frame interval [i+1] versus frame interval [i]

This plots tells us if there is a connection or correlation between errors in successive frame arrival times.

In [19]:
print 'number of frame intervals = ', frameInterval_time.shape[0]

# this assumes we have an even number
interval0 = frameInterval_time[0::2]
interval1 = frameInterval_time[1::2]

fig = {
    'data': [{
        'x': interval0, 
        'y': interval1, 
        'text': '', 
        'mode': 'markers', 
        'name': 'gpio'
    }],
    'layout': {
        'xaxis': {'title': 'Previous Inter-Frame-Interval'},
        'yaxis': {'title': "Inter-Frame-Interval (seconds)"}
    }
}

iplot(fig, filename='pandas/multiple-scatter')

number of frame intervals =  9991


And again with pigpio frame times.

In [20]:
print 'number of frame intervals = ', frameInterval_time.shape[0]

# this assumes we have an even number
interval0 = frameInterval_pigpio[0::2]
interval1 = frameInterval_pigpio[1::2]

fig = {
    'data': [{
        'x': interval0, 
        'y': interval1, 
        'text': '', 
        'mode': 'markers', 
        'name': 'pigpio'
    }],
    'layout': {
        'xaxis': {'title': 'Previous Inter-Frame-Interval'},
        'yaxis': {'title': "Inter-Frame-Interval (seconds)"}
    }
}

iplot(fig, filename='pandas/multiple-scatter')

number of frame intervals =  9991
